In [1]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler
from sklearn.metrics import roc_curve, auc
from sklearn.ensemble import GradientBoostingClassifier
from sklearn.model_selection import RandomizedSearchCV
from sklearn.model_selection import cross_val_score
from sklearn import metrics
from keras import Sequential
from keras.layers import Dense
from keras.layers import Input
from keras.utils.np_utils import to_categorical
from sklearn.metrics import roc_curve, auc
from keras.callbacks import EarlyStopping
from keras.wrappers.scikit_learn import KerasClassifier
from sklearn.model_selection import GridSearchCV

In [2]:
df = pd.read_csv("compare.csv")

X = df.drop(["home_win"], axis=1)
y = df.home_win.ravel()
X_train, X_test, y_train, y_test = train_test_split(X, y)
scaler = StandardScaler().fit(X_train)
X_train = scaler.transform(X_train)
X_test = scaler.transform(X_test)

In [3]:
# adjust format of inputs for neural network classifier
predictors = np.matrix(X_train)
target = to_categorical(y_train)
X_val = np.matrix(X_test)
y_val = to_categorical(y_test)

In [4]:
model = Sequential()
model.add(Input(shape=(14,)))
for x in range(16):
    model.add(Dense(128, activation='relu'))
model.add(Dense(2, activation='softmax'))
model.compile(optimizer='adam',loss='categorical_crossentropy',metrics=['accuracy'])

In [5]:
callbacks = [
    EarlyStopping(
        # Stop training when `val_loss` is no longer improving
        monitor="val_loss",
        # "no longer improving" being defined as "no better than 1e-3 less"
        min_delta=1e-3,
        # "no longer improving" being further defined as "for at least 5 epochs"
        patience=3,
        verbose=1,
    )
]
model.fit(predictors,target,batch_size=64,epochs=100,validation_data=(X_val, y_val),callbacks=callbacks)

Epoch 1/100
267/267 [==============================] - 1s 3ms/step - loss: 0.6364 - accuracy: 0.6403 - val_loss: 0.6263 - val_accuracy: 0.6581
Epoch 2/100
267/267 [==============================] - 1s 3ms/step - loss: 0.6251 - accuracy: 0.6519 - val_loss: 0.6232 - val_accuracy: 0.6537
Epoch 3/100
267/267 [==============================] - 1s 3ms/step - loss: 0.6225 - accuracy: 0.6563 - val_loss: 0.6217 - val_accuracy: 0.6575
Epoch 4/100
267/267 [==============================] - 1s 3ms/step - loss: 0.6204 - accuracy: 0.6585 - val_loss: 0.6198 - val_accuracy: 0.6568
Epoch 5/100
267/267 [==============================] - 1s 3ms/step - loss: 0.6171 - accuracy: 0.6607 - val_loss: 0.6224 - val_accuracy: 0.6602
Epoch 6/100
267/267 [==============================] - 1s 3ms/step - loss: 0.6156 - accuracy: 0.6613 - val_loss: 0.6230 - val_accuracy: 0.6556
Epoch 7/100
267/267 [==============================] - 1s 3ms/step - loss: 0.6116 - accuracy: 0.6675 - val_loss: 0.6293 - val_accuracy: 0.6554

In [6]:
y_pred = model.predict(X_val)
predictions = pd.DataFrame(y_pred, columns=['home_loss','home_win'])
predictions['binary'] = predictions['home_win'] > 0.5
y_pred = np.array(predictions['binary'])
false_positive_rate, true_positive_rate, thresholds = roc_curve(y_test, y_pred)
roc_auc = auc(false_positive_rate, true_positive_rate)
print("Neural Net's AUROC= " + str(round(roc_auc,3)), model.summary())

Model: "sequential"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
dense (Dense)                (None, 128)               1920      
_________________________________________________________________
dense_1 (Dense)              (None, 128)               16512     
_________________________________________________________________
dense_2 (Dense)              (None, 128)               16512     
_________________________________________________________________
dense_3 (Dense)              (None, 128)               16512     
_________________________________________________________________
dense_4 (Dense)              (None, 128)               16512     
_________________________________________________________________
dense_5 (Dense)              (None, 128)               16512     
_________________________________________________________________
dense_6 (Dense)              (None, 128)               1

In [7]:
# function to create + fit model, required for KerasClassifier

def create_model(layers,nodes,activation,batch_size):
    model = Sequential()
    model.add(Input(shape=(14,)))
    for x in range(layers):
        model.add(Dense(nodes, activation=activation))
    model.add(Dense(2, activation='softmax'))
    model.compile(optimizer='adam',loss='categorical_crossentropy',metrics=['accuracy'])
    model.fit(predictors,target,batch_size=batch_size,epochs=50,validation_data=(X_val, y_val),callbacks=callbacks,verbose=0)
    return model

In [8]:
model = KerasClassifier(build_fn=create_model, verbose=1)

In [9]:
layers= [2,4,8,16]
nodes= [32,64,128,256]
activation = ['relu','sigmoid','softmax','softplus','softsign','tanh','selu','elu','exponential']
batch_size = [10,25,50,75,100]
param_grid = dict(layers=layers,nodes=nodes,activation=activation,batch_size=batch_size)

In [10]:
grid = GridSearchCV(estimator=model,param_grid=param_grid,cv=5)

In [11]:
grid_result=grid.fit(X_train,y_train)
print("Best: %f using %s" % (grid_result.best_score_, grid_result.best_params_))
means = grid_result.cv_results_['mean_test_score']
stds = grid_result.cv_results_['std_test_score']
params = grid_result.cv_results_['params']
for mean, stdev, param in zip(means, stds, params):
    print("%f (%f) with: %r" % (mean, stdev, param))

Epoch 00008: early stopping
342/342 [==============================] - 0s 467us/step - loss: 0.6190 - accuracy: 0.6523
Epoch 00007: early stopping
342/342 [==============================] - 0s 475us/step - loss: 0.6092 - accuracy: 0.6610
Epoch 00005: early stopping
342/342 [==============================] - 0s 481us/step - loss: 0.6029 - accuracy: 0.6721
Epoch 00008: early stopping
342/342 [==============================] - 0s 468us/step - loss: 0.6116 - accuracy: 0.6713
Epoch 00004: early stopping
342/342 [==============================] - 0s 469us/step - loss: 0.6141 - accuracy: 0.6628
Epoch 00005: early stopping
342/342 [==============================] - 0s 472us/step - loss: 0.6174 - accuracy: 0.6517
Epoch 00004: early stopping
342/342 [==============================] - 0s 467us/step - loss: 0.6219 - accuracy: 0.6490
Epoch 00005: early stopping
342/342 [==============================] - 0s 472us/step - loss: 0.6021 - accuracy: 0.6780
Epoch 00006: early stopping
342/342 [===========

342/342 [==============================] - 0s 522us/step - loss: 0.6151 - accuracy: 0.6622
Epoch 00004: early stopping
342/342 [==============================] - 0s 502us/step - loss: 0.6124 - accuracy: 0.6727
Epoch 00004: early stopping
342/342 [==============================] - 0s 487us/step - loss: 0.6223 - accuracy: 0.6584
Epoch 00007: early stopping
342/342 [==============================] - 0s 502us/step - loss: 0.6129 - accuracy: 0.6619
Epoch 00005: early stopping
342/342 [==============================] - 0s 557us/step - loss: 0.6268 - accuracy: 0.6512
Epoch 00008: early stopping
342/342 [==============================] - 0s 539us/step - loss: 0.6230 - accuracy: 0.6534
Epoch 00006: early stopping
342/342 [==============================] - 0s 493us/step - loss: 0.6156 - accuracy: 0.6718
Epoch 00007: early stopping
342/342 [==============================] - 0s 516us/step - loss: 0.6219 - accuracy: 0.6499
Epoch 00008: early stopping
342/342 [==============================] - 0s 51

137/137 [==============================] - 0s 473us/step - loss: 0.6112 - accuracy: 0.6642
Epoch 00006: early stopping
137/137 [==============================] - 0s 480us/step - loss: 0.5975 - accuracy: 0.6797
Epoch 00005: early stopping
137/137 [==============================] - 0s 502us/step - loss: 0.6170 - accuracy: 0.6649
Epoch 00005: early stopping
137/137 [==============================] - 0s 488us/step - loss: 0.6074 - accuracy: 0.6633
Epoch 00004: early stopping
137/137 [==============================] - 0s 502us/step - loss: 0.6021 - accuracy: 0.6660
Epoch 00006: early stopping
137/137 [==============================] - 0s 514us/step - loss: 0.6144 - accuracy: 0.6584
Epoch 00005: early stopping
137/137 [==============================] - 0s 524us/step - loss: 0.6048 - accuracy: 0.6777
Epoch 00006: early stopping
137/137 [==============================] - 0s 480us/step - loss: 0.6225 - accuracy: 0.6567
Epoch 00007: early stopping
137/137 [==============================] - 0s 48

137/137 [==============================] - 0s 1ms/step - loss: 0.6160 - accuracy: 0.6622
Epoch 00010: early stopping
137/137 [==============================] - 0s 1ms/step - loss: 0.6214 - accuracy: 0.6493
Epoch 00007: early stopping
137/137 [==============================] - 0s 1ms/step - loss: 0.6211 - accuracy: 0.6581
Epoch 00006: early stopping
69/69 [==============================] - 0s 520us/step - loss: 0.6221 - accuracy: 0.6500
Epoch 00007: early stopping
69/69 [==============================] - 0s 477us/step - loss: 0.6139 - accuracy: 0.6639
Epoch 00005: early stopping
69/69 [==============================] - 0s 463us/step - loss: 0.6073 - accuracy: 0.6695
Epoch 00007: early stopping
69/69 [==============================] - 0s 491us/step - loss: 0.6164 - accuracy: 0.6633
Epoch 00007: early stopping
69/69 [==============================] - 0s 477us/step - loss: 0.6097 - accuracy: 0.6598
Epoch 00006: early stopping
69/69 [==============================] - 0s 477us/step - loss: 0

69/69 [==============================] - 0s 491us/step - loss: 0.5990 - accuracy: 0.6759
Epoch 00007: early stopping
69/69 [==============================] - 0s 527us/step - loss: 0.6090 - accuracy: 0.6661
Epoch 00004: early stopping
69/69 [==============================] - 0s 520us/step - loss: 0.6079 - accuracy: 0.6575
Epoch 00005: early stopping
69/69 [==============================] - 0s 520us/step - loss: 0.6080 - accuracy: 0.6610
Epoch 00004: early stopping
69/69 [==============================] - 0s 549us/step - loss: 0.6095 - accuracy: 0.6587
Epoch 00005: early stopping
69/69 [==============================] - 0s 491us/step - loss: 0.5989 - accuracy: 0.6724
Epoch 00004: early stopping
69/69 [==============================] - 0s 679us/step - loss: 0.6266 - accuracy: 0.6623
Epoch 00005: early stopping
69/69 [==============================] - 0s 636us/step - loss: 0.6128 - accuracy: 0.6715
Epoch 00004: early stopping
69/69 [==============================] - 0s 694us/step - loss: 0

...

69/69 [==============================] - 0s 514us/step - loss: nan - accuracy: 0.3946
Epoch 00003: early stopping
69/69 [==============================] - 0s 497us/step - loss: nan - accuracy: 0.4043
Epoch 00003: early stopping
69/69 [==============================] - 0s 482us/step - loss: nan - accuracy: 0.3893
Epoch 00003: early stopping
69/69 [==============================] - 0s 497us/step - loss: nan - accuracy: 0.4132
Epoch 00003: early stopping
69/69 [==============================] - 0s 542us/step - loss: nan - accuracy: 0.4087
Epoch 00003: early stopping
69/69 [==============================] - 0s 529us/step - loss: nan - accuracy: 0.3946
Epoch 00003: early stopping
69/69 [==============================] - 0s 526us/step - loss: nan - accuracy: 0.4043
Epoch 00003: early stopping
69/69 [==============================] - 0s 513us/step - loss: nan - accuracy: 0.3893
Epoch 00003: early stopping
69/69 [==============================] - 0s 745us/step - loss: nan - accuracy: 0.4132
Ep

46/46 [==============================] - 0s 486us/step - loss: nan - accuracy: 0.4087
Epoch 00003: early stopping
46/46 [==============================] - 0s 508us/step - loss: nan - accuracy: 0.3946
Epoch 00003: early stopping
46/46 [==============================] - 0s 465us/step - loss: nan - accuracy: 0.4043
Epoch 00003: early stopping
46/46 [==============================] - 0s 482us/step - loss: nan - accuracy: 0.3893
Epoch 00003: early stopping
46/46 [==============================] - 0s 507us/step - loss: nan - accuracy: 0.4132
Epoch 00003: early stopping
46/46 [==============================] - 0s 485us/step - loss: nan - accuracy: 0.4087
Epoch 00003: early stopping
46/46 [==============================] - 0s 486us/step - loss: nan - accuracy: 0.3946
Epoch 00003: early stopping
46/46 [==============================] - 0s 460us/step - loss: nan - accuracy: 0.4043
Epoch 00003: early stopping
46/46 [==============================] - 0s 462us/step - loss: nan - accuracy: 0.3893
Ep

46/46 [==============================] - 0s 1ms/step - loss: nan - accuracy: 0.4043
Epoch 00003: early stopping
46/46 [==============================] - 0s 1ms/step - loss: nan - accuracy: 0.3893
Epoch 00003: early stopping
46/46 [==============================] - 0s 526us/step - loss: nan - accuracy: 0.4132
Epoch 00003: early stopping
46/46 [==============================] - 0s 760us/step - loss: nan - accuracy: 0.4087
Epoch 00003: early stopping
46/46 [==============================] - 0s 507us/step - loss: nan - accuracy: 0.3946
Epoch 00003: early stopping
46/46 [==============================] - 0s 506us/step - loss: nan - accuracy: 0.4043
Epoch 00003: early stopping
46/46 [==============================] - 0s 529us/step - loss: nan - accuracy: 0.3893
Epoch 00003: early stopping
46/46 [==============================] - 0s 589us/step - loss: nan - accuracy: 0.4132
Epoch 00003: early stopping
46/46 [==============================] - 0s 804us/step - loss: nan - accuracy: 0.4087
Epoch 

35/35 [==============================] - 0s 780us/step - loss: nan - accuracy: 0.4043
Epoch 00003: early stopping
35/35 [==============================] - 0s 780us/step - loss: nan - accuracy: 0.3893
Epoch 00003: early stopping
35/35 [==============================] - 0s 2ms/step - loss: nan - accuracy: 0.4132
Epoch 00003: early stopping
35/35 [==============================] - 0s 2ms/step - loss: nan - accuracy: 0.4087
Epoch 00003: early stopping
35/35 [==============================] - 0s 2ms/step - loss: nan - accuracy: 0.3946
Epoch 00003: early stopping
35/35 [==============================] - 0s 2ms/step - loss: nan - accuracy: 0.4043
Epoch 00003: early stopping
35/35 [==============================] - 0s 2ms/step - loss: nan - accuracy: 0.3893
Epoch 00003: early stopping
35/35 [==============================] - 0s 552us/step - loss: nan - accuracy: 0.4132
Epoch 00003: early stopping
35/35 [==============================] - 0s 548us/step - loss: nan - accuracy: 0.4087
Epoch 00003:

0.658920 (0.008001) with: {'activation': 'tanh', 'batch_size': 100, 'layers': 4, 'nodes': 64}
0.655056 (0.005051) with: {'activation': 'tanh', 'batch_size': 100, 'layers': 4, 'nodes': 128}
0.650138 (0.004224) with: {'activation': 'tanh', 'batch_size': 100, 'layers': 4, 'nodes': 256}
0.659213 (0.009261) with: {'activation': 'tanh', 'batch_size': 100, 'layers': 8, 'nodes': 32}
0.658978 (0.008884) with: {'activation': 'tanh', 'batch_size': 100, 'layers': 8, 'nodes': 64}
0.653768 (0.008736) with: {'activation': 'tanh', 'batch_size': 100, 'layers': 8, 'nodes': 128}
0.651308 (0.006252) with: {'activation': 'tanh', 'batch_size': 100, 'layers': 8, 'nodes': 256}
0.653182 (0.006900) with: {'activation': 'tanh', 'batch_size': 100, 'layers': 16, 'nodes': 32}
0.656929 (0.007656) with: {'activation': 'tanh', 'batch_size': 100, 'layers': 16, 'nodes': 64}
0.622214 (0.026546) with: {'activation': 'tanh', 'batch_size': 100, 'layers': 16, 'nodes': 128}
0.608453 (0.009566) with: {'activation': 'tanh', 'ba

In [ ]:
Best: 0.677303 using {'activation': 'relu', 'batch_size': 100, 'layers': 8, 'nodes': 64}

In [12]:
# finalize tuned model from above GridSearch
NN = create_model(8,64,'relu',100)
# check AUROC for model using best params from the GridSearch
y_pred = NN.predict(X_val)
predictions = pd.DataFrame(y_pred, columns=['home_loss','home_win'])
predictions['binary'] = predictions['home_win'] > 0.5
y_pred = np.array(predictions['binary'])
false_positive_rate, true_positive_rate, thresholds = roc_curve(y_test, y_pred)
roc_auc = auc(false_positive_rate, true_positive_rate)
print("Tuned Neural Net's AUROC= " + str(round(roc_auc,3)))

Epoch 00005: early stopping
Tuned Neural Net's AUROC= 0.619


In [14]:
# redefine create_model, but with sigmoid as final and optimizer as param
def create_model(layers,nodes,activation,batch_size,optimizer):
    model = Sequential()
    model.add(Input(shape=(14,)))
    for x in range(layers):
        model.add(Dense(nodes, activation=activation))
    model.add(Dense(2, activation='sigmoid'))
    model.compile(optimizer=optimizer,loss='categorical_crossentropy',metrics=['accuracy'])
    model.fit(predictors,target,batch_size=batch_size,epochs=50,validation_data=(X_val, y_val),callbacks=callbacks,verbose=0)
    return model

In [20]:
# based on the first grid search, a new grid search with sigmoid as final func
layers= [6,7,8,9,10]
nodes= [52,58,64,70,76]
activation = ['relu','sigmoid','softmax','softplus','softsign','tanh','selu','elu']
batch_size = [75,100,125,200]
optimizer = ['SGD','RMSprop','Adam','Adadelta','Adagrad','Adamax','Nadam','Ftrl']
param_grid = dict(layers=layers,nodes=nodes,activation=activation,batch_size=batch_size,optimizer=optimizer)

In [21]:
model = KerasClassifier(build_fn=create_model, verbose=1)

In [22]:
grid = GridSearchCV(estimator=model,param_grid=param_grid,cv=5)

In [23]:
grid_result=grid.fit(X_train,y_train)
print("Best: %f using %s" % (grid_result.best_score_, grid_result.best_params_))
means = grid_result.cv_results_['mean_test_score']
stds = grid_result.cv_results_['std_test_score']
params = grid_result.cv_results_['params']
for mean, stdev, param in zip(means, stds, params):
    print("%f (%f) with: %r" % (mean, stdev, param))

Epoch 00021: early stopping
46/46 [==============================] - 0s 542us/step - loss: 0.6257 - accuracy: 0.6500
Epoch 00022: early stopping
46/46 [==============================] - 0s 564us/step - loss: 0.6186 - accuracy: 0.6601
Epoch 00024: early stopping
46/46 [==============================] - 0s 564us/step - loss: 0.6085 - accuracy: 0.6686
Epoch 00021: early stopping
46/46 [==============================] - 0s 520us/step - loss: 0.6203 - accuracy: 0.6534
Epoch 00023: early stopping
46/46 [==============================] - 0s 564us/step - loss: 0.6177 - accuracy: 0.6590
Epoch 00005: early stopping
46/46 [==============================] - 0s 542us/step - loss: 0.6223 - accuracy: 0.6599
Epoch 00007: early stopping
46/46 [==============================] - 0s 564us/step - loss: 0.6045 - accuracy: 0.6751
Epoch 00007: early stopping
46/46 [==============================] - 0s 542us/step - loss: 0.5973 - accuracy: 0.6812
Epoch 00005: early stopping
46/46 [=============================

46/46 [==============================] - 0s 607us/step - loss: 0.5903 - accuracy: 0.6894
Epoch 00004: early stopping
46/46 [==============================] - 0s 542us/step - loss: 0.6056 - accuracy: 0.6704
Epoch 00009: early stopping
46/46 [==============================] - 0s 564us/step - loss: 0.5953 - accuracy: 0.6876
Epoch 00005: early stopping
46/46 [==============================] - 0s 564us/step - loss: 0.6112 - accuracy: 0.6660
Epoch 00009: early stopping
46/46 [==============================] - 0s 542us/step - loss: 0.6878 - accuracy: 0.5868
Epoch 00009: early stopping
46/46 [==============================] - 0s 542us/step - loss: 0.6874 - accuracy: 0.5913
Epoch 00009: early stopping
46/46 [==============================] - 0s 607us/step - loss: 0.6864 - accuracy: 0.6054
Epoch 00009: early stopping
46/46 [==============================] - 0s 542us/step - loss: 0.6871 - accuracy: 0.5957
Epoch 00009: early stopping
46/46 [==============================] - 0s 563us/step - loss: 0

Epoch 00009: early stopping
46/46 [==============================] - 0s 520us/step - loss: 0.5941 - accuracy: 0.6736
Epoch 00006: early stopping
46/46 [==============================] - 0s 520us/step - loss: 0.6134 - accuracy: 0.6613
Epoch 00007: early stopping
46/46 [==============================] - 0s 542us/step - loss: 0.6044 - accuracy: 0.6704
Epoch 00006: early stopping
46/46 [==============================] - 0s 542us/step - loss: 0.6118 - accuracy: 0.6596
Epoch 00006: early stopping
46/46 [==============================] - 0s 520us/step - loss: 0.6080 - accuracy: 0.6695
Epoch 00005: early stopping
46/46 [==============================] - 0s 520us/step - loss: 0.6008 - accuracy: 0.6718
Epoch 00004: early stopping
46/46 [==============================] - 0s 520us/step - loss: 0.6120 - accuracy: 0.6669
Epoch 00004: early stopping
46/46 [==============================] - 0s 542us/step - loss: 0.6113 - accuracy: 0.6642
Epoch 00009: early stopping
46/46 [=============================

46/46 [==============================] - 0s 578us/step - loss: 0.6443 - accuracy: 0.6107
Epoch 00034: early stopping
46/46 [==============================] - 0s 607us/step - loss: 0.6316 - accuracy: 0.6430
Epoch 00041: early stopping
46/46 [==============================] - 0s 635us/step - loss: 0.6257 - accuracy: 0.6554
Epoch 00046: early stopping
46/46 [==============================] - 0s 486us/step - loss: 0.6143 - accuracy: 0.6604
Epoch 00041: early stopping
46/46 [==============================] - 0s 612us/step - loss: 0.6238 - accuracy: 0.6581
Epoch 00036: early stopping
46/46 [==============================] - 0s 570us/step - loss: 0.6223 - accuracy: 0.6575
Epoch 00008: early stopping
46/46 [==============================] - 0s 812us/step - loss: 0.6137 - accuracy: 0.6678
Epoch 00005: early stopping
46/46 [==============================] - 0s 609us/step - loss: 0.6075 - accuracy: 0.6683
Epoch 00005: early stopping
46/46 [==============================] - 0s 583us/step - loss: 0

46/46 [==============================] - 0s 776us/step - loss: 0.6155 - accuracy: 0.6643
Epoch 00006: early stopping
46/46 [==============================] - 0s 588us/step - loss: 0.6078 - accuracy: 0.6683
Epoch 00008: early stopping
46/46 [==============================] - 0s 615us/step - loss: 0.5942 - accuracy: 0.6812
Epoch 00005: early stopping
46/46 [==============================] - 0s 602us/step - loss: 0.6129 - accuracy: 0.6692
Epoch 00005: early stopping
46/46 [==============================] - 0s 604us/step - loss: 0.6706 - accuracy: 0.5868
Epoch 00028: early stopping
46/46 [==============================] - 0s 906us/step - loss: 0.6857 - accuracy: 0.5919
Epoch 00016: early stopping
46/46 [==============================] - 0s 615us/step - loss: 0.6560 - accuracy: 0.5957
Epoch 00042: early stopping
46/46 [==============================] - 0s 386us/step - loss: 0.6623 - accuracy: 0.6107
Epoch 00044: early stopping
46/46 [==============================] - 0s 415us/step - loss: 0

...

18/18 [==============================] - 0s 2ms/step - loss: 0.6170 - accuracy: 0.6531
Epoch 00005: early stopping
18/18 [==============================] - 0s 1ms/step - loss: 0.6269 - accuracy: 0.6512
Epoch 00006: early stopping
18/18 [==============================] - 0s 1ms/step - loss: 0.6155 - accuracy: 0.6645
Epoch 00006: early stopping
18/18 [==============================] - 0s 808us/step - loss: 0.6075 - accuracy: 0.6777
Epoch 00005: early stopping
18/18 [==============================] - 0s 341us/step - loss: 0.6215 - accuracy: 0.6505
Epoch 00005: early stopping
18/18 [==============================] - 0s 4ms/step - loss: 0.6138 - accuracy: 0.6563
Epoch 00008: early stopping
18/18 [==============================] - 0s 1ms/step - loss: 0.6295 - accuracy: 0.6441
Epoch 00007: early stopping
18/18 [==============================] - 0s 1ms/step - loss: 0.6178 - accuracy: 0.6584
Epoch 00007: early stopping
18/18 [==============================] - 0s 1ms/step - loss: 0.6137 - accura

18/18 [==============================] - 0s 1ms/step - loss: 0.6237 - accuracy: 0.6534
Epoch 00017: early stopping
18/18 [==============================] - 0s 1ms/step - loss: 0.6158 - accuracy: 0.6537
Epoch 00006: early stopping
18/18 [==============================] - 0s 1ms/step - loss: 0.6269 - accuracy: 0.6465
Epoch 00004: early stopping
18/18 [==============================] - 0s 1ms/step - loss: 0.6161 - accuracy: 0.6575
Epoch 00008: early stopping
18/18 [==============================] - 0s 1ms/step - loss: 0.6085 - accuracy: 0.6730
Epoch 00005: early stopping
18/18 [==============================] - 0s 1ms/step - loss: 0.6198 - accuracy: 0.6566
Epoch 00006: early stopping
18/18 [==============================] - 0s 1ms/step - loss: 0.6119 - accuracy: 0.6595
Epoch 00006: early stopping
18/18 [==============================] - 0s 1ms/step - loss: 0.6303 - accuracy: 0.6503
Epoch 00005: early stopping
18/18 [==============================] - 0s 1ms/step - loss: 0.6226 - accuracy: 

0.444180 (0.081002) with: {'activation': 'softmax', 'batch_size': 75, 'layers': 10, 'nodes': 58, 'optimizer': 'Adadelta'}
0.597975 (0.008836) with: {'activation': 'softmax', 'batch_size': 75, 'layers': 10, 'nodes': 58, 'optimizer': 'Adagrad'}
0.597975 (0.008836) with: {'activation': 'softmax', 'batch_size': 75, 'layers': 10, 'nodes': 58, 'optimizer': 'Adamax'}
0.597975 (0.008836) with: {'activation': 'softmax', 'batch_size': 75, 'layers': 10, 'nodes': 58, 'optimizer': 'Nadam'}
0.597975 (0.008836) with: {'activation': 'softmax', 'batch_size': 75, 'layers': 10, 'nodes': 58, 'optimizer': 'Ftrl'}
0.597975 (0.008836) with: {'activation': 'softmax', 'batch_size': 75, 'layers': 10, 'nodes': 64, 'optimizer': 'SGD'}
0.597975 (0.008836) with: {'activation': 'softmax', 'batch_size': 75, 'layers': 10, 'nodes': 64, 'optimizer': 'RMSprop'}
0.597975 (0.008836) with: {'activation': 'softmax', 'batch_size': 75, 'layers': 10, 'nodes': 64, 'optimizer': 'Adam'}
0.523151 (0.095610) with: {'activation': 'so

0.655699 (0.007269) with: {'activation': 'softsign', 'batch_size': 75, 'layers': 9, 'nodes': 76, 'optimizer': 'Adagrad'}
0.658393 (0.007127) with: {'activation': 'softsign', 'batch_size': 75, 'layers': 9, 'nodes': 76, 'optimizer': 'Adamax'}
0.654296 (0.013264) with: {'activation': 'softsign', 'batch_size': 75, 'layers': 9, 'nodes': 76, 'optimizer': 'Nadam'}
0.597975 (0.008836) with: {'activation': 'softsign', 'batch_size': 75, 'layers': 9, 'nodes': 76, 'optimizer': 'Ftrl'}
0.657690 (0.006916) with: {'activation': 'softsign', 'batch_size': 75, 'layers': 10, 'nodes': 52, 'optimizer': 'SGD'}
0.654588 (0.007706) with: {'activation': 'softsign', 'batch_size': 75, 'layers': 10, 'nodes': 52, 'optimizer': 'RMSprop'}
0.657690 (0.002719) with: {'activation': 'softsign', 'batch_size': 75, 'layers': 10, 'nodes': 52, 'optimizer': 'Adam'}
0.650313 (0.003469) with: {'activation': 'softsign', 'batch_size': 75, 'layers': 10, 'nodes': 52, 'optimizer': 'Adadelta'}
0.657222 (0.007338) with: {'activation':

0.655114 (0.009190) with: {'activation': 'elu', 'batch_size': 100, 'layers': 10, 'nodes': 58, 'optimizer': 'RMSprop'}
0.658568 (0.006695) with: {'activation': 'elu', 'batch_size': 100, 'layers': 10, 'nodes': 58, 'optimizer': 'Adam'}
0.648908 (0.001123) with: {'activation': 'elu', 'batch_size': 100, 'layers': 10, 'nodes': 58, 'optimizer': 'Adadelta'}
0.656754 (0.007945) with: {'activation': 'elu', 'batch_size': 100, 'layers': 10, 'nodes': 58, 'optimizer': 'Adagrad'}
0.660793 (0.006950) with: {'activation': 'elu', 'batch_size': 100, 'layers': 10, 'nodes': 58, 'optimizer': 'Adamax'}
0.656168 (0.005846) with: {'activation': 'elu', 'batch_size': 100, 'layers': 10, 'nodes': 58, 'optimizer': 'Nadam'}
0.597975 (0.008836) with: {'activation': 'elu', 'batch_size': 100, 'layers': 10, 'nodes': 58, 'optimizer': 'Ftrl'}
0.656285 (0.009757) with: {'activation': 'elu', 'batch_size': 100, 'layers': 10, 'nodes': 64, 'optimizer': 'SGD'}
0.656929 (0.005119) with: {'activation': 'elu', 'batch_size': 100, '

In [ ]:
'''
Epoch 00007: early stopping
183/183 [==============================] - 0s 2ms/step - loss: 0.5943 - accuracy: 0.6809
46/46 [==============================] - 0s 403us/step - loss: 0.5999 - accuracy: 0.6812
'''